In [ ]:
### import libraries
import numpy as np
import pandas as pd
import scanpy as sc
import scanpy.external as sce
import scipy
import sceleto2 as scl
import anndata, bbknn
import scrublet as scr
from harmony import harmonize

### plotting
import matplotlib.pyplot as plt
import seaborn as sns

import os, pickle, glob
import sys, time, random, math
from tqdm import notebook

### warnings
import warnings
from numba.core.errors import NumbaDeprecationWarning
warnings.filterwarnings(action="ignore", category=NumbaDeprecationWarning)
warnings.filterwarnings(
    action="ignore", module="scanpy", message="No data for colormapping"
)
warnings.simplefilter(action='ignore', category=FutureWarning)


### version
from platform import python_version
print('Python ', python_version(), end='\n')
sc.logging.print_version_and_date()
sc.logging.print_header()

In [ ]:
### settings
sc.settings.verbosity = 3 # verbosity: errors (0), warnings (1), info (2), hints (3)
#sc.settings.set_figure_params(dpi=100, color_map='OrRd', facecolor='white') 

In [ ]:
def RawCountsPreprocessing(adata):
    # HVG
    sc.pp.highly_variable_genes(adata)
    print(f"detected {np.sum(adata.var['highly_variable'])} highly variable genes") # 2992 HVGs

    print("="*100)


    # scaling
    print('scaling ...')
    sc.pp.scale(adata, max_value=10)

    print('max: ', np.max(adata.X))
    print('min: ', np.min(adata.X))
    print('mean: ', np.mean(adata.X))
    print("="*100)


    # cell cycle score
    cell_cycle_genes = [x.strip().capitalize() 
                        for x in open('/home/seoylee/myproject/study/scRNAseq/RegressionofCellCycle/regev_lab_cell_cycle_genes.txt')]
    s_genes = cell_cycle_genes[:43]
    g2m_genes = cell_cycle_genes[43:]
    sc.tl.score_genes_cell_cycle(adata, s_genes, g2m_genes)

    print("="*100)

    # remove cell cycle genes in HVG
    # mouse cell cycle genes list to remove
    geneset = [x.strip().capitalize() for x in open('/home/seoylee/script/mspark/20210308_Mouse_cell_cycle_gene_list_MS.txt')]
    geneset = [x for x in geneset if x in adata.var_names]

    print('remove {} cell cycle genes in HVG ...'.format(adata.var[adata.var_names.isin(geneset)]['highly_variable'].value_counts()[True]))
    adata.var.loc[geneset, 'highly_variable'] = False
    
    print("="*100)
    
    ### PCA
    sc.tl.pca(adata)
    
    return adata

In [ ]:
random.seed(2222)

# import data

##### atlas data

In [ ]:
atlas = sc.read('../Write/ECAtlas_normalization_11tissues.h5ad')
atlas.shape

In [ ]:
scl.us(atlas, 'Tissue,Endothelial cell,Cluster', wspace = 0.4)

In [ ]:
# remove not endothelial cell
atlas = atlas[atlas.obs['Endothelial cell'] == 'Yes']
atlas.shape

##### more robust annotation

probabilistic similarity를 계산할 때 사용한 annotation 으로 변경

In [ ]:
# raw data
backup = atlas.copy()
atlas = atlas.raw.to_adata()
atlas.raw = atlas.copy()
atlas.layers['counts'] = backup.layers['counts'].copy()

# pre-processing
atlas = RawCountsPreprocessing(atlas)

# no batch correction
sc.pp.neighbors(atlas, n_pcs = 17) # 그러봤을 때 PCs=17이 제일 이쁨
sc.tl.umap(atlas)

# n_pcs = 17
sc.pl.umap(atlas, color='Tissue,Cluster'.split(','))

In [ ]:
sc.tl.leiden(atlas, resolution=0.5, key_added='leiden_0.5')

In [ ]:
scl.us(atlas, 'leiden_0.5,Tissue,Cluster', wspace = 0.4)

In [ ]:
### lymphatic
sc.pl.umap(atlas, color = 'leiden_0.5', groups = ['7'])

In [ ]:
# heart, muscle
sc.pl.umap(atlas, color = ['Tissue'], groups = ['heart', 'muscle_edl', 'muscle_sol'])

In [ ]:
# intestine
sc.pl.umap(atlas, color = ['Tissue'], groups = ['intestine_colon', 'intestine_small'])

##### annotation

In [ ]:
# lymphatic
atlas.obs['Annotation'] = np.where(atlas.obs['leiden_0.5'] == '7', 'lymphatic', atlas.obs['Tissue'])

# heart + muscle_edl + muscle_sol
opt = ['muscle_sol', 'muscle_edl', 'heart']
atlas.obs['Annotation'] = np.where(atlas.obs['Annotation'].isin(opt), 'muscle/heart', atlas.obs['Annotation'])

# intestine = colon + small
atlas.obs['Annotation'] = np.where(atlas.obs['Annotation'].str.contains('intestine'), 'intestine', atlas.obs['Annotation'])

# UMAP
scl.us(atlas, 'Tissue,Annotation')

In [ ]:
## write
atlas.write('../Write/240820_atlas_robustAnnotation.h5ad')

##### FiNi-seq old sample

In [ ]:
fini = sc.read('/nfs/SCMGL/kyt01_liver/share/publish/endoold.h5ad')
fini.shape

In [ ]:
sc.pl.umap(fini, color = ['annotation_ENDO_publish'])

In [ ]:
fini_new =  sc.read('/nfs/SCMGL/kyt01_liver/share/publish/endonewold.h5ad') # endo new old only
fini_new.shape

In [ ]:
scl.us(fini_new, 'annotation_endonew_publish',)

# data integration 

In [ ]:
# raw
atlas = atlas.raw.to_adata()
atlas.raw = atlas.copy()

fini = fini.raw.to_adata()
fini.raw = fini.copy()


print('atlas =============================================')
print(np.max(atlas.X))
print(np.min(atlas.X))
print(np.mean(atlas.X))

print('FiNi ==============================================')
print(np.max(fini.X))
print(np.min(fini.X))
print(np.mean(fini.X))

In [ ]:
### scale check ;  every cell's total count
# atlas
df1 = atlas.to_df().to_numpy()
df1 = np.expm1(df1)
print('atals : ', df1.sum(axis=1)) # 10,000

# FiNi
df2 = fini.to_df().to_numpy()
df2 = np.expm1(df2)
print('FiNi-seq : ', df2.sum(axis=1)) #  approximately 100,000

normalize_total 의 target_sum이 다름

## total sum check

In [ ]:
# match scale -> atlas data target sum X10
df1 = df1 * 10
df1.sum(axis=1)

In [ ]:
atlas.X = scipy.sparse.csr_matrix(np.log1p(df1))
atlas.raw = atlas.copy()

## check
print('atlas =============================================')
print(np.max(atlas.X))
print(np.min(atlas.X))
print(np.mean(atlas.X))

print('FiNi ==============================================')
print(np.max(fini.X))
print(np.min(fini.X))
print(np.mean(fini.X))

In [ ]:
fig, ax = plt.subplots(ncols=2, figsize=(10,5))
sc.pl.violin(atlas, keys=['Gapdh'], show=False, ax=ax[0])
sc.pl.violin(fini, keys=['Gapdh'], show=False, ax=ax[1])
plt.show()

count 비슷함

## concat 

In [ ]:
### make refer column
atlas.obs['Refer'] = 'Atlas'
fini.obs['Refer'] = 'FiNi'

### concatenate inner join
adata = atlas.concatenate(fini, join = 'inner', index_unique=None, batch_key='Refer')
adata.shape

In [ ]:
adata = RawCountsPreprocessing(adata)

In [ ]:
sc.pl.pca_variance_ratio(adata, log=True)

n_pcs = 20으로 결정

In [ ]:
backup = adata.copy()

## batch correction 

In [ ]:
# harmony
sce.pp.harmony_integrate(adata, 'Refer',
                        adjusted_basis='X_pca_harmony')
sc.pp.neighbors(adata, n_pcs =20, use_rep='X_pca_harmony') ### .obsp['connectivities']  -> sc.tl.draw_graph 
sc.tl.umap(adata)

In [ ]:
scl.us(adata, 'Refer,Annotation,annotation_ENDO_publish,Cluster', wspace=0.37, ncols=2)

In [ ]:
sc.pl.umap(adata, color = ['annotation_ENDO_publish', 'Cluster'], groups = ['capillary arterial', 'large artery', 'PV'])

In [ ]:
## write
adata.write('../Write/240821_ECatlas-oldFiNi_combined_v01.h5ad')

## draw_graph 

In [ ]:
adata = sc.read('../Write/240821_ECatlas-oldFiNi_combined_v01.h5ad')

In [ ]:
sc.tl.draw_graph(adata, n_jobs=16)

In [ ]:
scl.us(adata, 'Refer,Annotation,annotation_ENDO_publish,Cluster', wspace=0.37, ncols=2)

In [ ]:
sc.pl.draw_graph(adata, color = 'Refer')
sc.pl.draw_graph(adata, color = 'Annotation')
sc.pl.draw_graph(adata, color = 'annotation_ENDO_publish')

In [ ]:
sc.pl.draw_graph(adata, color= ['Stab1', 'Stab2', 'Scarb2', 'Fcgr2b', 'Mrc1'])

##### fibrotic EC와 겹치는 organ만 따로 뗴서 진행

# subset 

In [ ]:
### make refer column
atlas.obs['Refer'] = 'Atlas'
fini.obs['Refer'] = 'FiNi'

In [ ]:
### subset
a = atlas[atlas.obs['Annotation'].isin(['muscle/heart', 'intestine', 'kidney', 'liver', 'lymphatic'])]
sc.pl.umap(a, color = ['Tissue','Annotation'])

In [ ]:
print(a.shape)
print(fini.shape)

In [ ]:
### concatenate inner join
adata = a.concatenate(fini, join = 'inner', index_unique=None, batch_key='Refer')
adata.shape

In [ ]:
adata = RawCountsPreprocessing(adata)

In [ ]:
sc.pl.pca_variance_ratio(adata, log=True)

n_pcs = 20으로 결정

In [ ]:
backup = adata.copy()

## batch correction 

In [ ]:
# harmony
sce.pp.harmony_integrate(adata, 'Refer',
                        adjusted_basis='X_pca_harmony')
sc.pp.neighbors(adata, n_pcs =20, use_rep='X_pca_harmony') ### .obsp['connectivities']  -> sc.tl.draw_graph 
sc.tl.umap(adata)

In [ ]:
scl.us(adata, 'Refer,Annotation,annotation_ENDO_publish,Cluster', wspace=0.37, ncols=2)

In [ ]:
sc.pp.neighbors(adata, n_pcs =30, use_rep='X_pca_harmony') ### .obsp['connectivities']  -> sc.tl.draw_graph 
sc.tl.umap(adata)

In [ ]:
scl.us(adata, 'Refer,Annotation,annotation_ENDO_publish,Cluster', wspace=0.37, ncols=2)

In [ ]:
sc.pl.umap(adata, color = 'Cluster', groups= ['large artery', 'artery', 'capillary arterial'])

In [ ]:
sc.pl.umap(adata, color = 'annotation_ENDO_publish', groups= ['PV', 'Fibrotic EC'])

In [ ]:
adata.obs['doublet_scores'] = adata.obs['doublet_scores'].astype('float')

In [ ]:
## write
adata.write('../Write/240821_ECatlasSubset-oldFiNi_combined_v01.h5ad')

## draw_graph

In [ ]:
adata = sc.read('../Write/240821_ECatlasSubset-oldFiNi_combined_v01.h5ad')

In [ ]:
sc.tl.draw_graph(adata, n_jobs=16)

In [ ]:
sc.pl.draw_graph(adata, color = 'Refer')
sc.pl.draw_graph(adata, color = 'Annotation')
sc.pl.draw_graph(adata, color = 'annotation_ENDO_publish')

In [ ]:
liver -> intestion
fibrotic EC:: additional function

In [ ]:
sc.pl.draw_graph(adata, color = 'Annotation', groups = 'liver')

In [ ]:
sc.pl.draw_graph(adata, color = 'Cluster', groups = ['large artery', 'artery', 'capillary arterial'])

In [ ]:
sc.pl.draw_graph(adata, color = 'Cluster',)

In [ ]:
sc.pl.draw_graph(adata, color = 'Cluster', groups = ['vein Madcam1+', 'large vein'])

In [ ]:
sc.pl.draw_graph(adata, color= ['Stab1', 'Stab2', 'Scarb2', 'Fcgr2b', 'Mrc1'])

##### fibrotic EC subset annotation tranfer

In [ ]:
scl.us(fini_new, 'annotation_endonew_publish',)

In [ ]:
print(len(fini.obs_names))
print(len(fini_new.obs_names))
len(set(fini.obs_names) & set(fini_new.obs_names))

In [ ]:
adata.obs = adata.obs.join(fini_new.obs['annotation_endonew_publish'])
fini.obs = fini.obs.join(fini_new.obs['annotation_endonew_publish'])

In [ ]:
sc.pl.umap(fini, color = ['annotation_ENDO_publish','annotation_endonew_publish'] )

In [ ]:
sc.pl.umap(adata, color = ['Refer', 'Annotation', 'annotation_ENDO_publish', 'annotation_endonew_publish'], ncols = 2)

In [ ]:
sc.pl.draw_graph(adata, color = ['Refer', 'Annotation', 'annotation_ENDO_publish', 'annotation_endonew_publish'], ncols = 2)

In [ ]:
for i in adata.obs['annotation_endonew_publish'].cat.categories:
    figure, axis = plt.subplots(1, 2, figsize= (13, 5))
    sc.pl.umap(adata, color = 'annotation_endonew_publish', groups = i, ax = axis[0], show=False)
    axis[0].get_legend().remove()
    sc.pl.draw_graph(adata, color = 'annotation_endonew_publish', groups = i, ax = axis[1], show=False)
    print()

force-directed graph 에서 leiden으로 cluster 잡은 후 liver만 가지고 trajectory

In [ ]:
sc.tl.leiden(adata, resolution=1, key_added ='leiden_1.0')
sc.tl.leiden(adata, resolution=2, key_added ='leiden_2.0')

In [ ]:
sc.tl.leiden(adata, resolution=1.5, key_added ='leiden_1.5')

In [ ]:
sc.pl.draw_graph(adata, color = ['leiden_1.0', 'leiden_1.5','leiden_2.0'])

In [ ]:
sc.pl.draw_graph(adata, color = 'leiden_1.5')

In [ ]:
# start
sc.pl.draw_graph(adata, color = 'leiden_1.5', groups = ['13', '1'])

In [ ]:
# mid
sc.pl.draw_graph(adata, color = 'leiden_1.5', groups = ['0', '17'])

In [ ]:
# end
sc.pl.draw_graph(adata, color = 'leiden_1.5', groups = '2,9'.split(','))

In [ ]:
# end
sc.pl.draw_graph(adata, color = 'leiden_2.0', groups = ',14'.split(','))

# Palantir; trajectories 

In [ ]:
import palantir

##### diffusion maps

In [ ]:
# run diffusion maps
dm_res = palantir.utils.run_diffusion_maps(adata, n_components=5)
ms_data = palantir.utils.determine_multiscale_space(adata)

In [ ]:
palantir.plot.plot_diffusion_components(adata)
plt.show()

##### Magic imputation 

In [ ]:
imputed_X = palantir.utils.run_magic_imputation(adata, n_jobs=32)

gene expression

In [ ]:
sc.pl.embedding(adata, basis = 'umap', layer = 'MAGIC_imputed_data', color = ['Col15a1', 'Sema3g', 'Sele', 'Lpl'])

In [ ]:
sc.pl.embedding(adata, basis = 'draw_graph_fa', layer = 'MAGIC_imputed_data', color = ['Col15a1', 'Sema3g', 'Sele', 'Lpl'])

In [ ]:
# PV marker
sc.pl.embedding(adata, basis = 'umap', layer = 'MAGIC_imputed_data', color = ['Gja5', 'Adgrg6', 'Nrg1'])
sc.pl.embedding(adata, basis = 'draw_graph_fa', layer = 'MAGIC_imputed_data', color = ['Gja5', 'Adgrg6', 'Nrg1'])

In [ ]:
scl.us(fini, 'annotation_ENDO_publish,annotation_endonew_publish,Gja5,Adgrg6,Nrg1', ncols=2)

##### end point set

In [ ]:
adata[:, adata.var.index == 'Sema3g'].X.argmax()

In [ ]:
adata[:, adata.var.index == 'Col15a1'].X.argmax()

In [ ]:
adata[:, adata.var.index == 'Lpl'].X.argmax()

In [ ]:
terminal_states = pd.Series(
    ["EC_Sema3g", "EC_Col15a1", "EC_Lpl"],
    index=[adata.obs.index[x] for x in [15291, 4656, 1358]],
)
palantir.plot.highlight_cells_on_umap(adata, terminal_states,  embedding_basis='X_draw_graph_fa')

##### start point set

In [ ]:
adata[:, adata.var.index == 'Adgrg6'].X.argmax()

In [ ]:
start_states = pd.Series(['PV'], index = [adata.obs.index[20639]])
palantir.plot.highlight_cells_on_umap(adata, start_states,  embedding_basis='X_draw_graph_fa')

## run trajectory 

In [ ]:
start_states.index

In [ ]:
start_cell = 'TGCGATATCATGGCCG-0-0'
pr_res = palantir.core.run_palantir(
    adata, start_cell, num_waypoints=500, terminal_states=terminal_states, n_jobs=8
)

Palantir generates the following results

1. Pseudotime: Pseudo time ordering of each cell
2. Terminal state probabilities: Matrix of cells X terminal states. Each entry represents the probability of the corresponding cell reaching the respective terminal state
3. Entropy: A quantiative measure of the differentiation potential of each cell computed as the entropy of the multinomial terminal state probabilities

In [ ]:
palantir.plot.plot_palantir_results(adata, s=3, embedding_basis = 'X_draw_graph_fa')
plt.show()

# FiNi-seq only trajectory 

In [ ]:
sc.pl.umap(fini, color = ['annotation_ENDO_publish', 'annotation_endonew_publish'])

In [ ]:
len(fini.obs_names[fini.obs['annotation_ENDO_publish'].isin(['PV', 'Fibrotic EC'])])

In [ ]:
len(fini_new.obs_names)

In [ ]:
set(fini.obs_names[fini.obs['annotation_ENDO_publish'].isin(['PV', 'Fibrotic EC'])]) == set(fini_new.obs_names)`

In [ ]:
idx = set(fini.obs_names[fini.obs['annotation_ENDO_publish'].isin(['PV', 'Fibrotic EC'])]) - set(fini_new.obs_names)
ax = sc.pl.umap(fini, show=False)
sc.pl.umap(fini[fini.obs_names.isin(idx)], color = 'annotation_ENDO_publish', ax = ax, size = 6)

In [ ]:
sc.pl.umap(fini_new, color = 'annotation_endonew_publish')

## PV + fibrotic EC 

In [ ]:
sc.tl.draw_graph(fini_new, n_jobs=16)

In [ ]:
sc.pl.draw_graph(fini_new, color=['annotation_endonew_publish'])

In [ ]:
sc.pl.draw_graph(fini_new, color=['annotation_endonew_publish', 'Clec1b', 'Aass']) # midzone: 'Clec1b', 'Aass'

LSEC 필요할 듯

In [ ]:
# PV marker
sc.pl.draw_graph(fini_new, color=['Gja5', 'Adgrg6', 'Nrg1'], ncols=3)

In [ ]:
fini_new[:, fini_new.var.index=='Adgrg6'].X.argmax()

In [ ]:
fini_new[:, fini_new.var.index=='Nrg1'].X.argmax()

In [ ]:
plt.grid(False)
sns.scatterplot(x = fini_new.obsm['X_draw_graph_fa'][:, 0], y = fini_new.obsm['X_draw_graph_fa'][:, 1],
               s=5, color ='lightgray')
sns.scatterplot(x = [fini_new.obsm['X_draw_graph_fa'][624, 0]], y = [fini_new.obsm['X_draw_graph_fa'][624, 1]], color='tab:blue')
sns.scatterplot(x = [fini_new.obsm['X_draw_graph_fa'][544, 0]], y = [fini_new.obsm['X_draw_graph_fa'][544, 1]], color = 'magenta')

In [ ]:
fini_new.uns['iroot'] = 624

In [ ]:
%%time
sc.tl.diffmap(fini_new)
sc.tl.dpt(fini_new)

In [ ]:
sc.pl.draw_graph(fini_new, color=['dpt_pseudotime'])

## PV + LSEC (midzone) + CV + fibrotic EC 

In [ ]:
subset = fini[fini.obs['annotation_ENDO_publish']!= 'Lymphatic EC']

In [ ]:
sc.pl.umap(subset, color = 'annotation_ENDO_publish')

In [ ]:
sc.tl.draw_graph(subset, n_jobs=16)

In [ ]:
sc.pl.draw_graph(subset, color=['annotation_ENDO_publish', 'annotation_endonew_publish'], ncols=2)

##### start point

In [ ]:
sc.pl.draw_graph(subset, color=['Clec1b', 'Aass'], ncols=2)

In [ ]:
subset[:, subset.var.index=='Clec1b'].X.argmax()

In [ ]:
subset[:, subset.var.index=='Aass'].X.argmax()

In [ ]:
plt.grid(False)
sns.scatterplot(x = subset.obsm['X_draw_graph_fa'][:, 0], y = subset.obsm['X_draw_graph_fa'][:, 1],
               s=3, color ='lightgray')
sns.scatterplot(x = [subset.obsm['X_draw_graph_fa'][2995, 0]], y = [subset.obsm['X_draw_graph_fa'][2995, 1]], color='tab:blue')
sns.scatterplot(x = [subset.obsm['X_draw_graph_fa'][7731, 0]], y = [subset.obsm['X_draw_graph_fa'][7731, 1]], color = 'magenta')

Clec1b 로 설정

## dpt (diffusion psuedotime)

7시 방향

In [ ]:
subset.uns['iroot'] = 2995

In [ ]:
%%time
sc.tl.diffmap(subset)
sc.tl.dpt(subset)

In [ ]:
sc.pl.draw_graph(subset, color=['dpt_pseudotime'])

In [ ]:
subset.uns['iroot'] = 2995

In [ ]:
%%time
sc.tl.diffmap(subset)
sc.tl.dpt(subset)

1시 방향

In [ ]:
subset.uns['iroot'] = 9683

In [ ]:
%%time
sc.tl.diffmap(subset)
sc.tl.dpt(subset)

In [ ]:
sc.pl.draw_graph(subset, color=['dpt_pseudotime'])

1시, 7시 어디로 잡든 CV, PV, Sema3g 가 맨 끝단으로 위치

In [ ]:
sc.pl.draw_graph(subset, color=['annotation_endonew_publish'])

Sema3g 쪽이 최종 끝지점처럼 나옴

In [ ]:
sc.tl.leiden(subset, resolution=1, key_added='leiden_1.0')
sc.pl.draw_graph(subset, color=['leiden_1.0'])

In [ ]:
sc.tl.leiden(subset, resolution=0.5, restrict_to=('leiden_1.0', ['5']))

In [ ]:
sc.pl.draw_graph(subset, color=['leiden_1.0', 'leiden_R'])

In [ ]:
fini_new.obs = fini_new.obs.join(subset.obs['leiden_R'])

In [ ]:
sc.pl.draw_graph(fini_new, color=['dpt_pseudotime', 'leiden_R'])

역시나 5,2 cluster가 제일 끝단

## palantir

In [ ]:
dm_res = palantir.utils.run_diffusion_maps(subset, n_components=5)
ms_data = palantir.utils.determine_multiscale_space(subset)

In [ ]:
imputed_X = palantir.utils.run_magic_imputation(subset, n_jobs=32)

In [ ]:
sc.pl.embedding(
    subset,
    basis="draw_graph_fa",
    layer="MAGIC_imputed_data",
    color=["Clec1b", 'Aass', # midzone marker ### 1시 방향이 count가 많나? imputated data에서 원래 raw count와 반대의 패턴 나옴
           'Wnt9b', 'Sema3g', 'Col15a1', 'Lpl', 'Sele'],
    frameon=False,
)

In [ ]:
sc.pl.draw_graph(subset, color = 'log1p_total_counts')

In [ ]:
sc.tl.leiden(subset, resolution=1, key_added='leiden_1.0')

In [ ]:
figure, axis = plt.subplots(1, 2, figsize= (10, 5))
sc.pl.umap(subset, color = 'leiden_1.0', ax = axis[0], show=False)
axis[0].get_legend().remove()
sc.pl.draw_graph(subset, color = 'leiden_1.0', ax = axis[1], show=False)

In [ ]:
palantir.plot.plot_diffusion_components(subset)

##### end point

midzone, LSEC

In [ ]:
sc.pl.draw_graph(subset, color = ['Clec1b', 'Aass', 'Bok', 'Fcgr2b', 'Scarb2'])

In [ ]:
subset[:, subset.var.index=='Fcgr2b'].X.argmax()

In [ ]:
plt.grid(False)
sns.scatterplot(x = subset.obsm['X_draw_graph_fa'][:, 0], y = subset.obsm['X_draw_graph_fa'][:, 1],
               s=3, color ='lightgray')
sns.scatterplot(x = [subset.obsm['X_draw_graph_fa'][5938, 0]], y = [subset.obsm['X_draw_graph_fa'][5938, 1]], color='tab:blue')

In [ ]:
idx = (subset.obsm['X_draw_graph_fa'][:, 0] >4400) & (subset.obsm['X_draw_graph_fa'][:, 0] <5500) 

In [ ]:
np.argmax(subset.obsm['X_draw_graph_fa'][idx, 1])

In [ ]:
values = subset.obsm['X_draw_graph_fa'][idx, 1][244]

In [ ]:
np.where(subset.obsm['X_draw_graph_fa'][:, 1] == values)

In [ ]:
plt.grid(False)
sns.scatterplot(x = subset.obsm['X_draw_graph_fa'][:, 0], y = subset.obsm['X_draw_graph_fa'][:, 1],
               s=3, color ='lightgray')
sns.scatterplot(x = [subset.obsm['X_draw_graph_fa'][9683, 0]], y = [subset.obsm['X_draw_graph_fa'][9683, 1]], color='tab:blue')

In [ ]:

subset.obsm['X_draw_graph_fa'][:, 0]

In [ ]:
np.argmin(subset.obsm['X_draw_graph_fa'][:, 0])

CV marker

In [ ]:
# CV marker
sc.pl.draw_graph(subset, color=['Wnt2', 'Wnt9b', 'Kit', 'Jpt1'], ncols=2)

In [ ]:
# CV marker
sc.pl.draw_graph(subset, color=['Lhx6', 'Ramp3', 'Rspo3', 'Vwf'], ncols=2)

In [ ]:
# CV marker
sc.pl.umap(subset, color=['Wnt2', 'Wnt9b', 'Kit', 'Jpt1',], ncols=2)

In [ ]:
subset[:, subset.var.index=='Wnt9b'].X.argmax()

In [ ]:
plt.grid(False)
sns.scatterplot(x = subset.obsm['X_draw_graph_fa'][:, 0], y = subset.obsm['X_draw_graph_fa'][:, 1],
               s=3, color ='lightgray')
sns.scatterplot(x = [subset.obsm['X_draw_graph_fa'][4537, 0]], y = [subset.obsm['X_draw_graph_fa'][4537, 1]], color='tab:blue')

In [ ]:
subset[:, subset.var.index=='Rspo3'].X.argmax()

In [ ]:
plt.grid(False)
sns.scatterplot(x = subset.obsm['X_draw_graph_fa'][:, 0], y = subset.obsm['X_draw_graph_fa'][:, 1],
               s=3, color ='lightgray')
sns.scatterplot(x = [subset.obsm['X_draw_graph_fa'][3152, 0]], y = [subset.obsm['X_draw_graph_fa'][3152, 1]], color='tab:blue')

In [ ]:
subset[:, subset.var.index=='Wnt2'].X.argmax()

In [ ]:
plt.grid(False)
sns.scatterplot(x = subset.obsm['X_draw_graph_fa'][:, 0], y = subset.obsm['X_draw_graph_fa'][:, 1],
               s=3, color ='lightgray')
sns.scatterplot(x = [subset.obsm['X_draw_graph_fa'][2243, 0]], y = [subset.obsm['X_draw_graph_fa'][2243, 1]], color='tab:blue')

In [ ]:
subset[:, subset.var.index=='Kit'].X.argmax()

In [ ]:
plt.grid(False)
sns.scatterplot(x = subset.obsm['X_draw_graph_fa'][:, 0], y = subset.obsm['X_draw_graph_fa'][:, 1],
               s=3, color ='lightgray')
sns.scatterplot(x = [subset.obsm['X_draw_graph_fa'][361, 0]], y = [subset.obsm['X_draw_graph_fa'][361, 1]], color='tab:blue')

In [ ]:
subset[:, subset.var.index=='Jpt1'].X.argmax()

In [ ]:
plt.grid(False)
sns.scatterplot(x = subset.obsm['X_draw_graph_fa'][:, 0], y = subset.obsm['X_draw_graph_fa'][:, 1],
               s=3, color ='lightgray')
sns.scatterplot(x = [subset.obsm['X_draw_graph_fa'][5352, 0]], y = [subset.obsm['X_draw_graph_fa'][5352, 1]], color='tab:blue')

umap 값 으로 점 찾기ㅠ

In [ ]:
np.argmin(subset.obsm['X_draw_graph_fa'][:, 0])

In [ ]:
plt.grid(False)
sns.scatterplot(x = subset.obsm['X_draw_graph_fa'][:, 0], y = subset.obsm['X_draw_graph_fa'][:, 1],
               s=3, color ='lightgray')
sns.scatterplot(x = [subset.obsm['X_draw_graph_fa'][9083, 0]], y = [subset.obsm['X_draw_graph_fa'][9083, 1]], color='tab:blue')

PV marker

In [ ]:
# PV marker
sc.pl.draw_graph(subset, color=['Gja5', 'Adgrg6', 'Nrg1'], ncols=3)

In [ ]:
subset[:, subset.var.index == 'Nrg1'].X.argmax()

In [ ]:
plt.grid(False)
sns.scatterplot(x = subset.obsm['X_draw_graph_fa'][:, 0], y = subset.obsm['X_draw_graph_fa'][:, 1],
               s=3, color ='lightgray')
sns.scatterplot(x = [subset.obsm['X_draw_graph_fa'][5270, 0]], y = [subset.obsm['X_draw_graph_fa'][5270, 1]], color='tab:blue')

fibrotic EC

In [ ]:

sc.pl.draw_graph(subset, color=['Sema3g', 'Col15a1', 'Lpl'], ncols=3)

In [ ]:
sc.pl.draw_graph(subset, color = 'annotation_endonew_publish', groups = 'Endo_Sele')

In [ ]:
sc.pl.draw_graph(subset, color = 'annotation_endonew_publish', groups = 'Endo_Lpl')

In [ ]:
a = subset[:, subset.var.index == 'Sema3g'].X.argmax()
a2 = subset[:, subset.var.index == 'Pdgfa'].X.argmax()

b = subset[:, subset.var.index == 'Col15a1'].X.argmax()
b2 = subset[:, subset.var.index == 'Col4a2'].X.argmax()

c = subset[:, subset.var.index == 'Lpl'].X.argmax()

In [ ]:
plt.grid(False)
sns.scatterplot(x = subset.obsm['X_draw_graph_fa'][:, 0], y = subset.obsm['X_draw_graph_fa'][:, 1],
               s=3, color ='lightgray')
sns.scatterplot(x = [subset.obsm['X_draw_graph_fa'][a, 0]], y = [subset.obsm['X_draw_graph_fa'][a, 1]], color='tab:blue')
sns.scatterplot(x = [subset.obsm['X_draw_graph_fa'][a2, 0]], y = [subset.obsm['X_draw_graph_fa'][a2, 1]], color='skyblue')

sns.scatterplot(x = [subset.obsm['X_draw_graph_fa'][b, 0]], y = [subset.obsm['X_draw_graph_fa'][b, 1]], color='magenta')
sns.scatterplot(x = [subset.obsm['X_draw_graph_fa'][b2, 0]], y = [subset.obsm['X_draw_graph_fa'][b2, 1]], color='pink')
sns.scatterplot(x = [subset.obsm['X_draw_graph_fa'][c, 0]], y = [subset.obsm['X_draw_graph_fa'][c, 1]], color='orange')

sema3g, col4a2 만 사용하는 것으로 결정

### run palantier

In [ ]:
terminal_states = pd.Series(
    ["CV", "PV", 'LSEC', "EC_Sema3g", "EC_Col15a1"],
    index=[subset.obs.index[x] for x in [9083, 5270, 9683, a, b2]],
)
palantir.plot.highlight_cells_on_umap(subset, terminal_states,  embedding_basis='X_draw_graph_fa')

In [ ]:
subset[:, subset.var.index=='Clec1b'].X.argmax()

In [ ]:
start_cell = subset.obs.index[2995]

pr_res = palantir.core.run_palantir(
    subset, start_cell, num_waypoints=500, terminal_states=terminal_states, n_jobs=32
)

In [ ]:
palantir.plot.plot_palantir_results(subset, s=2,  embedding_basis='X_draw_graph_fa')
plt.show()

In [ ]:
## LSEC 끝단에 없을 경우
palantir.plot.plot_palantir_results(subset, s=2,  embedding_basis='X_draw_graph_fa')
plt.show()

In [ ]:
terminal_states

In [ ]:
cells = [
    start_cell,
    terminal_states.index[0], # CV
    terminal_states.index[1], # PV
    terminal_states.index[2], # LSEC
#     terminal_states.index[3], # Sema3g
#     terminal_states.index[4], # Col15a1
]
plt.figure(figsize=(15,6))
palantir.plot.plot_terminal_state_probs(subset, cells)

for ax in plt.gcf().get_axes(): # 각 subplot 제어
    plt.sca(ax)
    plt.xticks(fontsize=10, rotation=90)
    plt.grid(False)
plt.show()

In [ ]:
cells = [
#     start_cell,
#     terminal_states.index[0], # CV
#     terminal_states.index[1], # PV
#     terminal_states.index[2], # LSEC
    terminal_states.index[3], # Sema3g
    terminal_states.index[4], # Col15a1
]
plt.figure(figsize=(15,6))
palantir.plot.plot_terminal_state_probs(subset, cells)

for ax in plt.gcf().get_axes(): # 각 subplot 제어
    plt.sca(ax)
    plt.xticks(fontsize=10, rotation=90)
    plt.grid(False)
plt.show()

In [ ]:
masks = palantir.presults.select_branch_cells(subset, q=.01, eps=.01)

In [ ]:
palantir.plot.plot_branch_selection(subset, embedding_basis='X_draw_graph_fa')
plt.show()

In [ ]:
palantir.plot.plot_trajectory(subset, "EC_Sema3g", embedding_basis='X_umap')

In [ ]:
palantir.plot.plot_trajectory(subset, "EC_Col15a1", embedding_basis='X_umap')

In [ ]:
palantir.plot.plot_trajectory(
    subset,
    "EC_Sema3g",
    cell_color="palantir_entropy",
    n_arrows=6,
    color="red",
    scanpy_kwargs=dict(cmap="viridis"),
    arrowprops=dict(arrowstyle="-|>,head_length=.5,head_width=.5"),
)

In [ ]:
palantir.plot.plot_trajectory(
    subset,
    "EC_Col15a1",
    cell_color="palantir_entropy",
    n_arrows=6,
    color="red",
    scanpy_kwargs=dict(cmap="viridis"),
    arrowprops=dict(arrowstyle="-|>,head_length=.5,head_width=.5"),
)

In [ ]:
sc.pl.umap(subset, color = 'annotation_endonew_publish')

In [ ]:
subset.write('../Write/240821_oldFiNi-subset_palantier_v01.h5ad')

## gene expression trends 

In [ ]:
sc.pl.embedding(
    subset,
    basis="draw_graph_fa",
    layer="MAGIC_imputed_data",
    color=["Clec1b", 'Aass', # midzone marker ### 1시 방향이 count가 많나? imputated data에서 원래 raw count와 반대의 패턴 나옴
           'Wnt9b', 'Sema3g', 'Col15a1', 'Lpl', 'Sele'],
    frameon=False,
)

In [ ]:
# marker trends
gene_trends = palantir.presults.compute_gene_trends(
    subset,
    expression_key="MAGIC_imputed_data",
)

In [ ]:
genes = ["Clec1b", 'Aass',
           'Wnt9b', 'Sema3g', 'Col15a1', 'Lpl', 'Sele']
palantir.plot.plot_gene_trends(subset, genes)
plt.show()

In [ ]:
palantir.plot.plot_gene_trend_heatmaps(subset, genes)
plt.show()

midzone을 end point에 두지 않으면 Clec1b, Aass 패턴이 이상하게 그려짐

### run palantier (endopoint: PV, CV, Sema3G)

In [ ]:
terminal_states = pd.Series(
    ["CV", "PV", 'LSEC', "EC_Sema3g"],
    index=[subset.obs.index[x] for x in [9083, 5270, 9683, a]],
)
palantir.plot.highlight_cells_on_umap(subset, terminal_states,  embedding_basis='X_draw_graph_fa')

In [ ]:
subset[:, subset.var.index=='Clec1b'].X.argmax()

In [ ]:
start_cell = subset.obs.index[2995]

pr_res = palantir.core.run_palantir(
    subset, start_cell, num_waypoints=500, terminal_states=terminal_states, n_jobs=32
)

In [ ]:
palantir.plot.plot_palantir_results(subset, s=2,  embedding_basis='X_draw_graph_fa')
plt.show()

In [ ]:
terminal_states

In [ ]:
cells = [
    start_cell,
    terminal_states.index[0], # CV
    terminal_states.index[1], # PV
    terminal_states.index[2], # LSEC
    terminal_states.index[3], # Sema3G
]
plt.figure(figsize=(15,6))
palantir.plot.plot_terminal_state_probs(subset, cells)

for ax in plt.gcf().get_axes(): # 각 subplot 제어
    plt.sca(ax)
    plt.xticks(fontsize=10, rotation=90)
    plt.grid(False)
plt.show()

In [ ]:
masks = palantir.presults.select_branch_cells(subset, q=.01, eps=.01)

In [ ]:
palantir.plot.plot_branch_selection(subset, embedding_basis='X_draw_graph_fa')
plt.show()

In [ ]:
palantir.plot.plot_trajectory(subset, "EC_Sema3g", embedding_basis='X_umap')

In [ ]:
palantir.plot.plot_trajectory(
    subset,
    "EC_Sema3g",
    cell_color="palantir_entropy",
    n_arrows=10,
    color="red",
    scanpy_kwargs=dict(cmap="viridis"),
    arrowprops=dict(arrowstyle="-|>,head_length=.5,head_width=.5"),
)

# trajectory (FiNi + EC atlas) 

In [ ]:
sc.pl.draw_graph(adata, color = ['Refer', 'Annotation', 'annotation_ENDO_publish', 'leiden_1.0'], ncols=2)

##### dpt

In [ ]:
sc.pl.draw_graph(adata, color=['Clec1b', 'Aass']) # midzone: 'Clec1b', 'Aass'

In [ ]:
adata[:, adata.var.index == 'Clec1b'].X.argmax()

In [ ]:
adata[:, adata.var.index == 'Aass'].X.argmax()

In [ ]:
plt.grid(False)
sns.scatterplot(x = adata.obsm['X_draw_graph_fa'][:, 0], y = adata.obsm['X_draw_graph_fa'][:, 1],
               s=5, color ='lightgray')
sns.scatterplot(x = [adata.obsm['X_draw_graph_fa'][14912, 0]], y = [adata.obsm['X_draw_graph_fa'][14912, 1]], color='tab:blue')
sns.scatterplot(x = [adata.obsm['X_draw_graph_fa'][19659, 0]], y = [adata.obsm['X_draw_graph_fa'][19659, 1]], color='magenta')

In [ ]:
adata.uns['iroot'] = 19659

In [ ]:
%%time
sc.tl.diffmap(adata)
sc.tl.dpt(adata)

In [ ]:
sc.pl.draw_graph(adata, color=['dpt_pseudotime'])

##### 필요없는 cluster 다 제외

In [ ]:
figure, axis = plt.subplots(1, 2, figsize= (13, 5))

sc.pl.umap(adata, color = 'leiden_1.0', ax = axis[0], show=False)
axis[0].get_legend().remove()
sc.pl.draw_graph(adata, color = 'leiden_1.0', ax = axis[1], show=False)

In [ ]:
sc.pl.umap(adata, color = ['Annotation', 'annotation_ENDO_publish'], show=False)

In [ ]:
sc.pl.draw_graph(adata, color = ['Annotation', 'annotation_ENDO_publish'], show=False)

In [ ]:
ccc = set(adata.obs['leiden_1.0']) - set('4,5,9,12,16'.split(','))

In [ ]:
figure, axis = plt.subplots(1, 2, figsize= (13, 5))

sc.pl.umap(adata, color = 'leiden_1.0', groups = ccc, ax = axis[0], show=False)
axis[0].get_legend().remove()
sc.pl.draw_graph(adata, color = 'leiden_1.0', groups = ccc, ax = axis[1], show=False)

In [ ]:
sc.pl.umap(adata, color = 'leiden_1.0', groups = '4,5,9,12,16'.split(','))

In [ ]:
for i in '4,5,9,10,12,16'.split(','): 
    ax = sc.pl.draw_graph(adata, show=False)
    sc.pl.draw_graph(adata[adata.obs['leiden_1.0']==i], color=['annotation_endonew_publish'], title=[i], ax=ax, size=10)

10은 포함하는걸로

In [ ]:
bdata = adata.copy()

In [ ]:
adata = adata[~adata.obs['leiden_1.0'].isin('4,5,9,12,16'.split(','))]
print(adata.shape)

In [ ]:
adata = adata.raw.to_adata()
adata.raw = adata.copy()

In [ ]:
adata = RawCountsPreprocessing(adata)

In [ ]:
sc.pl.pca_variance_ratio(adata, log=True)

n_pcs = 20으로 결정

In [ ]:
backup = adata.copy()

##### batch correction 

In [ ]:
# harmony
sce.pp.harmony_integrate(adata, 'Refer',
                        adjusted_basis='X_pca_harmony')

In [ ]:
sc.pp.neighbors(adata, n_pcs =30, use_rep='X_pca_harmony') ### .obsp['connectivities']  -> sc.tl.draw_graph 
sc.tl.umap(adata)

In [ ]:
scl.us(adata, 'status,sample,mouse,DQ')

In [ ]:
scl.us(adata, 'Refer,Annotation,Cluster,annotation_ENDO_publish,annotation_endonew_publish,leiden_1.0', wspace=0.37, ncols=2)

In [ ]:
sc.pl.umap(adata, color = ['annotation_ENDO_publish', 'Cluster'], groups = ['capillary arterial', 'large artery', 'PV'])

In [ ]:
## write
adata.write('../Write/240821_ECatlas-oldFiNi_combined_v01.h5ad')

## draw_graph 

In [ ]:
adata = sc.read('../Write/240821_ECatlas-oldFiNi_combined_v01.h5ad')

In [ ]:
sc.tl.draw_graph(adata, n_jobs=16)

In [ ]:
scl.us(adata, 'Refer,Annotation,annotation_ENDO_publish,Cluster', wspace=0.37, ncols=2)

In [ ]:
sc.pl.draw_graph(adata, color = 'Refer')
sc.pl.draw_graph(adata, color = 'Annotation')
sc.pl.draw_graph(adata, color = 'annotation_ENDO_publish')

In [ ]:
sc.pl.draw_graph(adata, color= ['Stab1', 'Stab2', 'Scarb2', 'Fcgr2b', 'Mrc1'])

##### fibrotic EC와 겹치는 organ만 따로 뗴서 진행

# subset 

In [ ]:
## check data form
print('atlas =============================================')
print(np.max(atlas.X))
print(np.min(atlas.X))
print(np.mean(atlas.X))

print('FiNi ==============================================')
print(np.max(fini.X))
print(np.min(fini.X))
print(np.mean(fini.X))

In [ ]:
sc.pl.umap(atlas, color =['Annotation', 'leiden_0.5', 'Cluster'])

In [ ]:
### subset
a = atlas[atlas.obs['Annotation'].isin(['muscle/heart', 'intestine', 'liver'])]
a = a[a.obs['leiden_0.5']!= '11'] # exclude heart specific cluster (large vein)
sc.pl.umap(a, color = ['Tissue','Annotation'])

In [ ]:
### subset
f = fini[fini.obs['annotation_ENDO_publish'].isin(['PV', 'Midzone', 'Fibrotic EC', 'CV'])]
sc.pl.umap(f, color = 'annotation_ENDO_publish')

In [ ]:
print(a.shape)
print(f.shape)

In [ ]:
### concatenate inner join
adata = a.concatenate(f, join = 'inner', index_unique=None, batch_key='Refer')
adata.shape

In [ ]:
adata = RawCountsPreprocessing(adata)

In [ ]:
sc.pl.pca_variance_ratio(adata, log=True)

In [ ]:
backup = adata.copy()

##### batch correction 

In [ ]:
# harmony
sce.pp.harmony_integrate(adata, 'Refer',
                        adjusted_basis='X_pca_harmony')

In [ ]:
sc.pp.neighbors(adata, n_pcs =20, use_rep='X_pca_harmony') ### .obsp['connectivities']  -> sc.tl.draw_graph 
sc.tl.umap(adata)

In [ ]:
scl.us(adata, 'Refer,Annotation,annotation_ENDO_publish,Cluster', wspace=0.37, ncols=2) # n_pcs = 20

In [ ]:
sc.tl.leiden(adata, resolution=1, key_added='leiden_1.0')
sc.tl.leiden(adata, resolution=0.5, key_added='leiden_0.5')

In [ ]:
scl.us(adata, 'leiden_1.0,leiden_0.5', wspace=0.37, ncols=2) # n_pcs = 20

In [ ]:
adata.obs['doublet_scores'] = adata.obs['doublet_scores'].astype('float')

In [ ]:
## write
adata.write('../Write/240828_ECatlas-oldFiNi_combined_v02.h5ad')

## draw_graph 

In [ ]:
?? sc.tl.draw_graph

In [ ]:
sc.tl.draw_graph(adata, n_jobs=16)

In [ ]:
sc.pl.draw_graph(adata, color = 'Refer')
sc.pl.draw_graph(adata, color = 'Annotation')
sc.pl.draw_graph(adata, color = 'annotation_ENDO_publish')

In [ ]:
sc.pl.draw_graph(adata, color = ['leiden_0.5', 'leiden_1.0'])

In [ ]:
## endocytosis-receptor genes
# scavenger receptors (Scarb2, Stab1, Stab2), a mannose receptor (Mrc1), and a lysosomal transport protein (Lamp2)
# Fc gamma-receptor IIb2 (Fcgr2b), which regulates the endocytosis
# This suggests that the endocytic and clearance functions of the Fibrotic ECs are compromised.
sc.pl.draw_graph(adata, color= ['Stab1', 'Stab2', 'Scarb2',  'Mrc1', 'Lamp2', 'Fcgr2b'])

In [ ]:
# endothelial cell
sc.pl.draw_graph(adata, color= ['Pecam1', 'Cdh5'])

In [ ]:
adata.obs = adata.obs.join(fini_new.obs['annotation_endonew_publish'])

In [ ]:
sc.pl.draw_graph(adata, color=['annotation_endonew_publish'])

In [ ]:
sc.pl.draw_graph(adata, color=['Clec1b', 'Aass', 'Bok'], cmap= 'Spectral_r') # midzone: 'Clec1b', 'Aass', 'Bok'

In [ ]:
adata[:, adata.var.index=='Clec1b'].X.argmax()

In [ ]:
adata[:, adata.var.index=='Aass'].X.argmax()

In [ ]:
## midzone LSEC marker

plt.grid(False)
sns.scatterplot(x = adata.obsm['X_draw_graph_fa'][:, 0], y = adata.obsm['X_draw_graph_fa'][:, 1],
               s=3, color ='lightgray')
sns.scatterplot(x = [adata.obsm['X_draw_graph_fa'][12286, 0]], y = [adata.obsm['X_draw_graph_fa'][12286, 1]], color='tab:blue')
sns.scatterplot(x = [adata.obsm['X_draw_graph_fa'][17022, 0]], y = [adata.obsm['X_draw_graph_fa'][17022, 1]], color='magenta')

In [ ]:
## scavenger funtion
sc.pl.draw_graph(adata, color='Stab1,Stab2,Scarb2,Fcgr2b,Mrc1,Robo1'.split(','), cmap= 'Spectral_r')

In [ ]:
g1 = adata[:, adata.var.index=='Stab1'].X.argmax()
g2 = adata[:, adata.var.index=='Stab2'].X.argmax()
g3 = adata[:, adata.var.index=='Scarb2'].X.argmax()

### Stab1, Stab2, Scarb2

plt.grid(False)
sns.scatterplot(x = adata.obsm['X_draw_graph_fa'][:, 0], y = adata.obsm['X_draw_graph_fa'][:, 1],
               s=3, color ='lightgray')
sns.scatterplot(x = [adata.obsm['X_draw_graph_fa'][g1, 0]], y = [adata.obsm['X_draw_graph_fa'][g1, 1]], color='tab:blue')
sns.scatterplot(x = [adata.obsm['X_draw_graph_fa'][g2, 0]], y = [adata.obsm['X_draw_graph_fa'][g2, 1]], color='magenta')
sns.scatterplot(x = [adata.obsm['X_draw_graph_fa'][g3, 0]], y = [adata.obsm['X_draw_graph_fa'][g3, 1]], color='orange')

In [ ]:
g1 = adata[:, adata.var.index=='Fcgr2b'].X.argmax()
g2 = adata[:, adata.var.index=='Mrc1'].X.argmax()

plt.grid(False)
sns.scatterplot(x = adata.obsm['X_draw_graph_fa'][:, 0], y = adata.obsm['X_draw_graph_fa'][:, 1],
               s=3, color ='lightgray')
sns.scatterplot(x = [adata.obsm['X_draw_graph_fa'][g1, 0]], y = [adata.obsm['X_draw_graph_fa'][g1, 1]], color='tab:blue')
sns.scatterplot(x = [adata.obsm['X_draw_graph_fa'][g2, 0]], y = [adata.obsm['X_draw_graph_fa'][g2, 1]], color='magenta')

In [ ]:
# rank genes
sc.tl.rank_genes_groups(adata, groupby='leiden_1.0', groups = ['5', '0', '2'], reference = 'rest', method='wilcoxon')

In [ ]:
dedf = sc.get.rank_genes_groups_df(adata, group = '5')
dedf

In [ ]:
sc.pl.draw_graph(adata, color = dedf['names'].head(10), cmap='Spectral_r')

In [ ]:
dedf = sc.get.rank_genes_groups_df(adata, group = '0')
dedf

In [ ]:
sc.pl.draw_graph(adata, color = dedf['names'].head(10), cmap='Spectral_r')

In [ ]:
m = scl.markers.marker(adata, 'leiden_1.0')

In [ ]:
marker = m.plot_marker()

In [ ]:
marker['0'], marker['2'], marker['4'], marker['7']

In [ ]:
marker['5']

In [ ]:
sc.pl.draw_graph(adata, color = marker['5'], cmap='Spectral_r')

## run dpt

In [ ]:
adata[:, adata.var.index=='Stab2'].X.argmax()

In [ ]:
## endocytosis receptor

plt.grid(False)
sns.scatterplot(x = adata.obsm['X_draw_graph_fa'][:, 0], y = adata.obsm['X_draw_graph_fa'][:, 1],
               s=3, color ='lightgray')
sns.scatterplot(x = [adata.obsm['X_draw_graph_fa'][12343, 0]], y = [adata.obsm['X_draw_graph_fa'][12343, 1]], color='tab:blue')

In [ ]:
## endocytosis receptor

plt.grid(False)
sns.scatterplot(x = adata.obsm['X_umap'][:, 0], y = adata.obsm['X_umap'][:, 1],
               s=3, color ='lightgray')
sns.scatterplot(x = [adata.obsm['X_umap'][12343, 0]], y = [adata.obsm['X_umap'][12343, 1]], color='tab:blue')

In [ ]:
adata.uns['iroot'] = 12343

In [ ]:
%%time
sc.tl.diffmap(adata)
sc.tl.dpt(adata)

In [ ]:
sc.pl.draw_graph(adata, color=['dpt_pseudotime'], cmap= 'Spectral_r')

In [ ]:
sc.pl.draw_graph(adata, color=[ 'annotation_ENDO_publish', 'annotation_endonew_publish', 'Annotation',], ncols=2, wspace=0.3)

In [ ]:
## imputated data
imputed_X[:, adata.var.index=='Clec1b'].argmax()

In [ ]:
## midzone LSEC marker

plt.grid(False)
sns.scatterplot(x = adata.obsm['X_draw_graph_fa'][:, 0], y = adata.obsm['X_draw_graph_fa'][:, 1],
               s=3, color ='lightgray')
sns.scatterplot(x = [adata.obsm['X_draw_graph_fa'][19072, 0]], y = [adata.obsm['X_draw_graph_fa'][19072, 1]], color='tab:blue')

In [ ]:
## midzone LSEC marker

plt.grid(False)
sns.scatterplot(x = adata.obsm['X_umap'][:, 0], y = adata.obsm['X_umap'][:, 1],
               s=3, color ='lightgray')
sns.scatterplot(x = [adata.obsm['X_umap'][19072, 0]], y = [adata.obsm['X_umap'][19072, 1]], color='tab:blue')

In [ ]:
adata.uns['iroot'] = 19072

In [ ]:
%%time
sc.tl.diffmap(adata)
sc.tl.dpt(adata)

In [ ]:
sc.pl.draw_graph(adata, color=['dpt_pseudotime'], cmap= 'Spectral_r')

In [ ]:
sc.pl.draw_graph(adata, color=[ 'annotation_ENDO_publish', 'annotation_endonew_publish', 'Annotation',], ncols=2, wspace=0.3)

## palantir 

In [ ]:
import palantir

In [ ]:
dm_res = palantir.utils.run_diffusion_maps(adata, n_components=5)
ms_data = palantir.utils.determine_multiscale_space(adata)

In [ ]:
imputed_X = palantir.utils.run_magic_imputation(adata, n_jobs=32)

In [ ]:
sc.pl.embedding(
    adata,
    basis="draw_graph_fa",
    layer="MAGIC_imputed_data",
    color=['Stab2', # iroot
           "Clec1b", 'Aass', # midzone marker ### imputated data에서 원래 raw count와 반대의 패턴 나옴, 아마도 count biased
           'Wnt9b', # CV marker
           'Gja5', 'Adgrg6', #PV marker
           'Sema3g', 'Col15a1', 'Lpl', 'Sele'],
    frameon=False,
)

In [ ]:
sc.pl.draw_graph(adata, color = ['log1p_total_counts', "Clec1b", 'Aass',])

In [ ]:
palantir.plot.plot_diffusion_components(adata)

In [ ]:
figure, axis = plt.subplots(1, 2, figsize= (13, 5))
sc.pl.umap(adata, color = 'leiden_0.5',  ax = axis[0], show=False)
sc.pl.draw_graph(adata, color = 'leiden_0.5', ax = axis[1], show=False)

In [ ]:
figure, axis = plt.subplots(1, 2, figsize= (13, 5))
sc.pl.umap(adata, color = 'annotation_endonew_publish',  ax = axis[0], show=False)
sc.pl.draw_graph(adata, color = 'annotation_endonew_publish', ax = axis[1], show=False)

In [ ]:
sc.pl.umap(adata, color = 'Annotation')

- component0 : Sele, connective spot
- component1 : non-liver dataset
- component2 : CV, PV
- component3 : intestine
- component4 : LSEC

##### end point 찾기
- LSEC
- CV
- PV
- fibrotic EC subannotation

1) LSEC

In [ ]:
## imputated data
imputed_X[:, adata.var.index=='Clec1b'].argmax()

In [ ]:
plt.grid(False)
sns.scatterplot(x = adata.obsm['X_draw_graph_fa'][:, 0], y = adata.obsm['X_draw_graph_fa'][:, 1],
               s=3, color ='lightgray')
sns.scatterplot(x = [adata.obsm['X_draw_graph_fa'][19072, 0]], y = [adata.obsm['X_draw_graph_fa'][19072, 1]], color='tab:blue')

2) CV

In [ ]:
## imputated data
imputed_X[:, adata.var.index=='Wnt9b'].argmax()

In [ ]:
plt.grid(False)
sns.scatterplot(x = adata.obsm['X_draw_graph_fa'][:, 0], y = adata.obsm['X_draw_graph_fa'][:, 1],
               s=3, color ='lightgray')
sns.scatterplot(x = [adata.obsm['X_draw_graph_fa'][6269, 0]], y = [adata.obsm['X_draw_graph_fa'][6269, 1]], color='tab:blue')

3) PV

In [ ]:
## imputated data
imputed_X[:, adata.var.index=='Gja5'].argmax()

In [ ]:
## imputated data
imputed_X[:, adata.var.index=='Adgrg6'].argmax()

In [ ]:
plt.grid(False)
sns.scatterplot(x = adata.obsm['X_draw_graph_fa'][:, 0], y = adata.obsm['X_draw_graph_fa'][:, 1],
               s=3, color ='lightgray')
sns.scatterplot(x = [adata.obsm['X_draw_graph_fa'][9666, 0]], y = [adata.obsm['X_draw_graph_fa'][9666, 1]], color='tab:blue')
sns.scatterplot(x = [adata.obsm['X_draw_graph_fa'][10955, 0]], y = [adata.obsm['X_draw_graph_fa'][10955, 1]], color='magenta')

.>>> Adgrg6로 결정

4) fibrotic EC

In [ ]:
g1 = imputed_X[:, adata.var.index=='Sema3g'].argmax()
g2 = imputed_X[:, adata.var.index=='Col15a1'].argmax()
g3 = imputed_X[:, adata.var.index=='Lpl'].argmax()

plt.grid(False)
sns.scatterplot(x = adata.obsm['X_draw_graph_fa'][:, 0], y = adata.obsm['X_draw_graph_fa'][:, 1],
               s=3, color ='lightgray')
sns.scatterplot(x = [adata.obsm['X_draw_graph_fa'][g1, 0]], y = [adata.obsm['X_draw_graph_fa'][g1, 1]], color='tab:blue')
sns.scatterplot(x = [adata.obsm['X_draw_graph_fa'][g2, 0]], y = [adata.obsm['X_draw_graph_fa'][g2, 1]], color='magenta')
sns.scatterplot(x = [adata.obsm['X_draw_graph_fa'][g3, 0]], y = [adata.obsm['X_draw_graph_fa'][g3, 1]], color='orange')

### run palantier

In [ ]:
terminal_states = pd.Series(
    ["CV", "PV", 'LSEC', "EC_Sema3g", "EC_Col15a1", "EC_Lpl"],
    index=[adata.obs.index[x] for x in [6269, 10955, 19072, g1, g2, g3]],
)

plt.close('all')
fig, ax = plt.subplots(figsize=(16,14))
palantir.plot.highlight_cells_on_umap(adata, terminal_states,  embedding_basis='X_draw_graph_fa', ax=ax)
plt.show()

In [ ]:
adata[:, adata.var.index=='Stab2'].X.argmax()

In [ ]:
def draw_maxGEX_cell(adata, gene_name, imputate=False):
    idx_num = adata[:, adata.var.index==gene_name].X.argmax()
    if imputate:
        idx_num = imputed_X[:, adata.var.index==gene_name].argmax()

    fig, ax = plt.subplots(ncols=2, figsize=(10,5))
    
    sns.scatterplot(x = adata.obsm['X_draw_graph_fa'][:, 0], y = adata.obsm['X_draw_graph_fa'][:, 1],
                    s=3, color ='lightgray', ax=ax[0])
    sns.scatterplot(x = [adata.obsm['X_draw_graph_fa'][idx_num, 0]], y = [adata.obsm['X_draw_graph_fa'][idx_num, 1]], color='tab:blue',
                   ax=ax[0])
    ax[0].set_title('force-directed graph')
    sns.scatterplot(x = adata.obsm['X_umap'][:, 0], y = adata.obsm['X_umap'][:, 1],
                    s=3, color ='lightgray', ax=ax[1])
    sns.scatterplot(x = [adata.obsm['X_umap'][idx_num, 0]], y = [adata.obsm['X_umap'][idx_num, 1]], color='tab:blue', ax=ax[1])
    ax[1].set_title('UMAP')
    
    ax[0].grid(False)
    ax[1].grid(False)
    plt.show()
    
    print(f'{gene_name} max cell idx = ', idx_num)

In [ ]:
draw_maxGEX_cell(adata, 'Stab2')

In [ ]:
start_cell = adata.obs.index[12343]

pr_res = palantir.core.run_palantir(
    adata, start_cell, num_waypoints=500, terminal_states=terminal_states, n_jobs=32
)

In [ ]:
palantir.plot.plot_palantir_results(adata, s=2,  embedding_basis='X_draw_graph_fa')
plt.show()

In [ ]:
terminal_states

In [ ]:
cells = [
    start_cell,
    terminal_states.index[0], # CV
    terminal_states.index[1], # PV
    terminal_states.index[2], # LSEC
#     terminal_states.index[3], # Sema3g
#     terminal_states.index[4], # Col15a1
]
plt.figure(figsize=(15,6))
palantir.plot.plot_terminal_state_probs(adata, cells)

for ax in plt.gcf().get_axes(): # 각 subplot 제어
    plt.sca(ax)
    plt.xticks(fontsize=10, rotation=90)
    plt.grid(False)
plt.show()

In [ ]:
cells = [
#     start_cell,
#     terminal_states.index[0], # CV
#     terminal_states.index[1], # PV
#     terminal_states.index[2], # LSEC
    terminal_states.index[3], # Sema3g
    terminal_states.index[4], # Col15a1
    terminal_states.index[5], # EC_Lpl
]
plt.figure(figsize=(15,6))
palantir.plot.plot_terminal_state_probs(adata, cells)

for ax in plt.gcf().get_axes(): # 각 subplot 제어
    plt.sca(ax)
    plt.xticks(fontsize=10, rotation=90)
    plt.grid(False)
plt.show()

In [ ]:
masks = palantir.presults.select_branch_cells(adata, q=.01, eps=.01)

In [ ]:
palantir.plot.plot_branch_selection(adata, embedding_basis='X_draw_graph_fa')
plt.show()

In [ ]:
palantir.plot.plot_trajectory(adata, "CV", embedding_basis='X_umap')

In [ ]:
palantir.plot.plot_trajectory(adata, "LSEC", embedding_basis='X_umap')

In [ ]:
palantir.plot.plot_trajectory(adata, "PV", embedding_basis='X_umap')

##### other option

In [ ]:
terminal_states = pd.Series(
    ["CV", "PV", 'LSEC', "EC_Sema3g", "EC_Col15a1", "EC_Lpl"],
    index=[adata.obs.index[x] for x in [6269, 10955, 12343, g1, g2, g3]],
)

plt.close('all')
fig, ax = plt.subplots(figsize=(16,14))
palantir.plot.highlight_cells_on_umap(adata, terminal_states,  embedding_basis='X_draw_graph_fa', ax=ax)
plt.show()

In [ ]:
## imputated data
imputed_X[:, adata.var.index=='Clec1b'].argmax()

In [ ]:
draw_maxGEX_cell(adata, 'Clec1b', imputate=True)

In [ ]:
draw_maxGEX_cell(adata, '', imputate=True)

In [ ]:
start_cell = adata.obs.index[19072]

pr_res = palantir.core.run_palantir(
    adata, start_cell, num_waypoints=500, terminal_states=terminal_states, n_jobs=32
)

In [ ]:
palantir.plot.plot_palantir_results(adata, s=2,  embedding_basis='X_draw_graph_fa')
plt.show()

In [ ]:
cells = [
    start_cell,
    terminal_states.index[0], # CV
    terminal_states.index[1], # PV
    terminal_states.index[2], # LSEC
#     terminal_states.index[3], # Sema3g
#     terminal_states.index[4], # Col15a1
]
plt.figure(figsize=(15,6))
palantir.plot.plot_terminal_state_probs(adata, cells)

for ax in plt.gcf().get_axes(): # 각 subplot 제어
    plt.sca(ax)
    plt.xticks(fontsize=10, rotation=90)
    plt.grid(False)
plt.show()

In [ ]:
cells = [
#     start_cell,
#     terminal_states.index[0], # CV
#     terminal_states.index[1], # PV
#     terminal_states.index[2], # LSEC
    terminal_states.index[3], # Sema3g
    terminal_states.index[4], # Col15a1
    terminal_states.index[5], # EC_Lpl
]
plt.figure(figsize=(15,6))
palantir.plot.plot_terminal_state_probs(adata, cells)

for ax in plt.gcf().get_axes(): # 각 subplot 제어
    plt.sca(ax)
    plt.xticks(fontsize=10, rotation=90)
    plt.grid(False)
plt.show()

In [ ]:
masks = palantir.presults.select_branch_cells(adata, q=.01, eps=.01)

In [ ]:
palantir.plot.plot_branch_selection(adata, embedding_basis='X_draw_graph_fa')
plt.show()

In [ ]:
palantir.plot.plot_trajectory(adata, "CV", embedding_basis='X_umap')

In [ ]:
palantir.plot.plot_trajectory(adata, "LSEC", embedding_basis='X_umap')

In [ ]:
palantir.plot.plot_trajectory(adata, "PV", embedding_basis='X_umap')

##### PV를 end point에서 제거

In [ ]:
terminal_states = pd.Series(
    ["CV", 'LSEC', "EC_Sema3g", "EC_Col15a1", "EC_Lpl"],
    index=[adata.obs.index[x] for x in [6269, 12343, g1, g2, g3]],
)

plt.close('all')
fig, ax = plt.subplots(figsize=(16,14))
palantir.plot.highlight_cells_on_umap(adata, terminal_states,  embedding_basis='X_draw_graph_fa', ax=ax)
plt.show()

In [ ]:
adata.uns['iroot']

In [ ]:
plt.grid(False)
sns.scatterplot(x = adata.obsm['X_draw_graph_fa'][:, 0], y = adata.obsm['X_draw_graph_fa'][:, 1],
               s=3, color ='lightgray')
sns.scatterplot(x = [adata.obsm['X_draw_graph_fa'][19072, 0]], y = [adata.obsm['X_draw_graph_fa'][19072, 1]], color='tab:blue')

In [ ]:
start_cell = adata.obs.index[19072]

pr_res = palantir.core.run_palantir(
    adata, start_cell, num_waypoints=500, terminal_states=terminal_states, n_jobs=32
)

In [ ]:
palantir.plot.plot_palantir_results(adata, s=2,  embedding_basis='X_draw_graph_fa')
plt.show()

In [ ]:
terminal_states

In [ ]:
cells = [
    start_cell,
    terminal_states.index[0], # CV
    terminal_states.index[1], # LSEC
]
plt.figure(figsize=(15,6))
palantir.plot.plot_terminal_state_probs(adata, cells)

for ax in plt.gcf().get_axes(): # 각 subplot 제어
    plt.sca(ax)
    plt.xticks(fontsize=10, rotation=90)
    plt.grid(False)
plt.show()

In [ ]:
cells = [
    terminal_states.index[2], # Sema3g
    terminal_states.index[3], # Col15a1
    terminal_states.index[4], # EC_Lpl
]
plt.figure(figsize=(15,6))
palantir.plot.plot_terminal_state_probs(adata, cells)

for ax in plt.gcf().get_axes(): # 각 subplot 제어
    plt.sca(ax)
    plt.xticks(fontsize=10, rotation=90)
    plt.grid(False)
plt.show()

In [ ]:
masks = palantir.presults.select_branch_cells(adata, q=.01, eps=.01)

In [ ]:
palantir.plot.plot_branch_selection(adata, embedding_basis='X_draw_graph_fa')
plt.show()

In [ ]:
palantir.plot.plot_trajectory(adata, "CV", embedding_basis='X_umap')

In [ ]:
palantir.plot.plot_trajectory(adata, "LSEC", embedding_basis='X_umap')

In [ ]:
palantir.plot.plot_trajectory(adata, "EC_Sema3g", embedding_basis='X_umap')

In [ ]:
palantir.plot.plot_trajectory(adata, "EC_Col15a1", embedding_basis='X_umap')

In [ ]:
palantir.plot.plot_trajectory(adata, "EC_Lpl", embedding_basis='X_umap')

### gene expression trends

In [ ]:
# marker trends
gene_trends = palantir.presults.compute_gene_trends(
    adata,
    expression_key="MAGIC_imputed_data",
)

In [ ]:
genes = ["Clec1b", 'Aass', # mid
           'Wnt9b', # CV
         'Gja5', 'Adgrg6', # PV
         'Sema3g', 'Col15a1', 'Lpl', 'Sele']
palantir.plot.plot_gene_trends(adata, genes)
plt.show()

PV marker가 CV 중간에 띄는게 이상함... PV가 잘 잡히도록 end point 설정하기!!!

***Sele***은 중간에 가장 높은 모양새가 확실히 fibrotic EC의 identity loss의 가장 첫 단계인 것 같음

***Sema3g***도 중간에 높았다가 내려감

UMAP상 여러 조직의 가운데에 위치한만큼 de-differentiation의 초기이지 않을까 싶음

그러다가 Col15a1처럼 특징적으로 ECM-secretion하는 population이 있는게 아닐까?

***col15a1***이 끝단 같음

In [ ]:
genes = ['Pecam1', 'Cdh5',
         'Stab1', 'Stab2', 'Scarb2',  'Mrc1', 'Lamp2', 'Fcgr2b']
palantir.plot.plot_gene_trends(adata, genes)
plt.show()

In [ ]:
sc.pl.umap(atlas, color = ['Annotation', 'Stab1', 'Stab2', 'Scarb2',  'Mrc1', 'Lamp2', 'Fcgr2b'], cmap='YlOrRd')

애초에 liver 이외의 tissue type에서 endocytosis-receptor genes 이 많이 뜨진 않음

In [ ]:
## write
adata.write('../Write/240828_ECatlas-oldFiNi_combined_v02.h5ad')

### run palantier

##### other option

Sema3g가 중간 단계인 것 같음, end point에서 제거

In [ ]:
terminal_states = pd.Series(
    ["CV", 'LSEC', "EC_Col15a1", "EC_Lpl"],
    index=[adata.obs.index[x] for x in [6269, 12343, g2, g3]],
)

plt.close('all')
fig, ax = plt.subplots(figsize=(16,14))
palantir.plot.highlight_cells_on_umap(adata, terminal_states,  embedding_basis='X_draw_graph_fa', ax=ax)
plt.show()

In [ ]:
## imputated data
imputed_X[:, adata.var.index=='Clec1b'].argmax()

In [ ]:
draw_maxGEX_cell(adata, 'Clec1b', imputate=True)

In [ ]:
start_cell = adata.obs.index[19072]

pr_res = palantir.core.run_palantir(
    adata, start_cell, num_waypoints=500, terminal_states=terminal_states, n_jobs=32
)

In [ ]:
palantir.plot.plot_palantir_results(adata, s=2,  embedding_basis='X_draw_graph_fa')
plt.show()

In [ ]:
terminal_states

In [ ]:
cells = [
    start_cell,
    terminal_states.index[0], # CV
    terminal_states.index[1], # LSEC
]
plt.figure(figsize=(15,6))
palantir.plot.plot_terminal_state_probs(adata, cells)

for ax in plt.gcf().get_axes(): # 각 subplot 제어
    plt.sca(ax)
    plt.xticks(fontsize=10, rotation=90)
    plt.grid(False)
plt.show()

In [ ]:
cells = [
    terminal_states.index[2], # Col15a1
    terminal_states.index[3], # EC_Lpl
]
plt.figure(figsize=(15,6))
palantir.plot.plot_terminal_state_probs(adata, cells)

for ax in plt.gcf().get_axes(): # 각 subplot 제어
    plt.sca(ax)
    plt.xticks(fontsize=10, rotation=90)
    plt.grid(False)
plt.show()

In [ ]:
masks = palantir.presults.select_branch_cells(adata, q=.01, eps=.01)

In [ ]:
palantir.plot.plot_branch_selection(adata, embedding_basis='X_draw_graph_fa')
plt.show()

In [ ]:
palantir.plot.plot_trajectory(adata, "CV", embedding_basis='X_umap')

In [ ]:
palantir.plot.plot_trajectory(adata, "LSEC", embedding_basis='X_umap')

In [ ]:
palantir.plot.plot_trajectory(adata, "EC_Col15a1", embedding_basis='X_umap')

In [ ]:
palantir.plot.plot_trajectory(adata, "EC_Lpl", embedding_basis='X_umap')

### gene expression trends

In [ ]:
# marker trends
gene_trends = palantir.presults.compute_gene_trends(
    adata,
    expression_key="MAGIC_imputed_data",
)

In [ ]:
genes = ["Clec1b", 'Aass', # mid
           'Wnt9b', # CV
         'Gja5', 'Adgrg6', # PV
         'Sema3g', 'Col15a1', 'Lpl', 'Sele']
palantir.plot.plot_gene_trends(adata, genes)
plt.show()

PV marker가 CV 중간에 띄고 있음, CV라는 cluster가 PV를 모두 포함하고 있음

In [ ]:
genes = ['Pecam1', 'Cdh5',
         'Stab1', 'Stab2', 'Scarb2',  'Mrc1', 'Lamp2', 'Fcgr2b']
palantir.plot.plot_gene_trends(adata, genes)
plt.show()

### run palantier

In [ ]:
sc.pl.draw_graph(adata, color = 'annotation_ENDO_publish', groups='CV')
sc.pl.draw_graph(adata, color = 'annotation_ENDO_publish', groups='PV')

##### other option

- Sema3g가 중간 단계인 것 같음, end point에서 제거

- LSEC 이 start인데 end point에 또 LSEC을 잡는게 불필요할 것 같음

In [ ]:
terminal_states = pd.Series(
    ["CV", "EC_Col15a1", "EC_Lpl"],
    index=[adata.obs.index[x] for x in [6269, g2, g3]],
)

plt.close('all')
fig, ax = plt.subplots(figsize=(16,14))
palantir.plot.highlight_cells_on_umap(adata, terminal_states,  embedding_basis='X_draw_graph_fa', ax=ax)
plt.show()

In [ ]:
draw_maxGEX_cell(adata, 'Clec1b', imputate=True)

In [ ]:
adata

In [ ]:
start_cell = adata.obs.index[19072]

pr_res = palantir.core.run_palantir(
    adata, start_cell, num_waypoints=500, terminal_states=terminal_states, n_jobs=32
)

In [ ]:
palantir.plot.plot_palantir_results(adata, s=2,  embedding_basis='X_draw_graph_fa')
plt.show()

In [ ]:
terminal_states

In [ ]:
cells = [
    start_cell,
    terminal_states.index[0], # CV
    terminal_states.index[1], # Col15a1
    terminal_states.index[2], # EC_Lpl
]
plt.figure(figsize=(15,6))
palantir.plot.plot_terminal_state_probs(adata, cells)

for ax in plt.gcf().get_axes(): # 각 subplot 제어
    plt.sca(ax)
    plt.xticks(fontsize=10, rotation=90)
    plt.grid(False)
plt.show()

In [ ]:
masks = palantir.presults.select_branch_cells(adata, q=.01, eps=.01)

In [ ]:
palantir.plot.plot_branch_selection(adata, embedding_basis='X_draw_graph_fa')
plt.show()

In [ ]:
palantir.plot.plot_trajectory(adata, "CV", embedding_basis='X_umap')

In [ ]:
palantir.plot.plot_trajectory(adata, "EC_Col15a1", embedding_basis='X_umap')

In [ ]:
palantir.plot.plot_trajectory(adata, "EC_Lpl", embedding_basis='X_umap')

### gene expression trends

In [ ]:
# marker trends
gene_trends = palantir.presults.compute_gene_trends(
    adata,
    expression_key="MAGIC_imputed_data",
)

In [ ]:
genes = ["Clec1b", 'Aass', # mid
           'Wnt9b', # CV
         'Gja5', 'Adgrg6', # PV
        ]
palantir.plot.plot_gene_trends(adata, genes)
plt.show()

PV marker가 CV 중간에 띄고 있음, CV라는 cluster가 PV를 모두 포함하고 있음

In [ ]:
genes = ['Sele', 'Sema3g', 'Col15a1', 'Lpl', ]
palantir.plot.plot_gene_trends(adata, genes)
plt.show()

Sele, Sema3g 는 중간에 위치

In [ ]:
genes = ['Pecam1', 'Cdh5',
         'Stab1', 'Stab2', 'Scarb2',  'Mrc1', 'Lamp2', 'Fcgr2b']
palantir.plot.plot_gene_trends(adata, genes)
plt.show()

In [ ]:
sc.pl.embedding(
    adata,
    basis="draw_graph_fa",
    layer="MAGIC_imputed_data",
    color=['Pecam1', 'Cdh5',
         'Stab1', 'Stab2', 'Scarb2',  'Mrc1', 'Lamp2', 'Fcgr2b'],
    frameon=False,
)

### run palantier

##### PV 끝점 다시 설정

In [ ]:
# PV
draw_maxGEX_cell(adata, 'Nrg1')

In [ ]:
# CV
draw_maxGEX_cell(adata, 'Wnt9b', imputate=True)

In [ ]:
terminal_states = pd.Series(
    ["CV", "PV", "EC_Col15a1", "EC_Lpl"],
    index=[adata.obs.index[x] for x in [6269, 3977, g2, g3]],
)

plt.close('all')
fig, ax = plt.subplots(figsize=(16,14))
palantir.plot.highlight_cells_on_umap(adata, terminal_states,  embedding_basis='X_draw_graph_fa', ax=ax)
plt.show()

In [ ]:
# start point
draw_maxGEX_cell(adata, 'Clec1b', imputate=True)

In [ ]:
start_cell = adata.obs.index[19072]

pr_res = palantir.core.run_palantir(
    adata, start_cell, num_waypoints=500, terminal_states=terminal_states, n_jobs=32
)

In [ ]:
palantir.plot.plot_palantir_results(adata, s=2,  embedding_basis='X_draw_graph_fa')
plt.show()

In [ ]:
terminal_states

In [ ]:
cells = [
    start_cell,
    terminal_states.index[0], # CV
    terminal_states.index[1], # PV
    terminal_states.index[2], # Col15a1
    terminal_states.index[3], # EC_Lpl
]
plt.figure(figsize=(15,6))
palantir.plot.plot_terminal_state_probs(adata, cells)

for ax in plt.gcf().get_axes(): # 각 subplot 제어
    plt.sca(ax)
    plt.xticks(fontsize=10, rotation=90)
    plt.grid(False)
plt.show()

In [ ]:
masks = palantir.presults.select_branch_cells(adata, q=.01, eps=.01)

In [ ]:
palantir.plot.plot_branch_selection(adata, embedding_basis='X_draw_graph_fa')
plt.show()

In [ ]:
palantir.plot.plot_trajectory(adata, "CV", embedding_basis='X_umap')

In [ ]:
palantir.plot.plot_trajectory(adata, 'PV', embedding_basis='X_umap')

In [ ]:
palantir.plot.plot_trajectory(adata, "EC_Col15a1", embedding_basis='X_umap')

In [ ]:
palantir.plot.plot_trajectory(adata, "EC_Col15a1", embedding_basis='X_umap',
                             cell_color= 'palantir_entropy',  scanpy_kwargs=dict(cmap="viridis"),)

In [ ]:
palantir.plot.plot_trajectory(adata, "EC_Lpl", embedding_basis='X_umap',
                              cell_color= 'palantir_entropy',  scanpy_kwargs=dict(cmap="viridis"))

### gene expression trends

In [ ]:
# marker trends
gene_trends = palantir.presults.compute_gene_trends(
    adata,
    expression_key="MAGIC_imputed_data",
)

In [ ]:
genes = ["Clec1b", 'Aass', # mid
           'Wnt9b', # CV
         'Gja5', 'Adgrg6', # PV
        ]
palantir.plot.plot_gene_trends(adata, genes)
plt.show()

PV 추가하니까 뭐.. 괜찮아 보임

In [ ]:
genes = ['Sele', 'Sema3g', 'Col15a1', 'Lpl', ]
palantir.plot.plot_gene_trends(adata, genes)
plt.show()

Sele, Sema3g 는 중간에 위치

In [ ]:
genes = ['Pecam1', 'Cdh5',
         'Stab1', 'Stab2', 'Scarb2',  'Mrc1', 'Lamp2', 'Fcgr2b']
palantir.plot.plot_gene_trends(adata, genes)
plt.show()

In [ ]:
palantir.plot.plot_gene_trend_heatmaps(adata, ["Clec1b", 'Aass', # mid
                                                'Wnt2', # CV
                                               'Gja5', 'Adgrg6', # PV
                                              ], cmap = 'viridis')

fig = plt.gcf() # 현재 모든 figure 가져오기
for ax in fig.get_axes(): # subplot에 모든 axes에 접근
    ax.grid(False)

plt.show()

EC 중간에 Gja5, Adgrg6가 뜨는걸로 봐서 둘은 PV를 중간 trajectory로 두고 있을 것

In [ ]:
palantir.plot.plot_gene_trend_heatmaps(adata, ['Stab1', 'Stab2', 'Scarb2', 'Fcgr2b', 'Mrc1'], cmap = 'viridis')

fig = plt.gcf() # 현재 모든 figure 가져오기
for ax in fig.get_axes(): # subplot에 모든 axes에 접근
    ax.grid(False)

plt.show()

CV, PV도 GEX 떨어지는 패턴

In [ ]:
sc.pl.umap(fini, color = ['Stab1', 'Stab2', 'Scarb2', 'Fcgr2b', 'Mrc1'], cmap = 'YlOrRd', ncols = 5)

In [ ]:
sc.pl.dotplot(fini, var_names= ['Stab1', 'Stab2', 'Scarb2', 'Fcgr2b', 'Mrc1'],
             groupby='annotation_ENDO_publish')

In [ ]:
sc.pl.umap(atlas, color = ['Stab1', 'Stab2', 'Scarb2', 'Fcgr2b', 'Mrc1'], cmap = 'YlOrRd', ncols = 5)

In [ ]:
sc.pl.dotplot(atlas, var_names= ['Stab1', 'Stab2', 'Scarb2', 'Fcgr2b', 'Mrc1'],
             groupby='Annotation')

In [ ]:
'Il6' in adata.var_names

In [ ]:
palantir.plot.plot_gene_trend_heatmaps(adata, ['Sele','Selp', 'Ackr1',
                                               'Sema3g', 'Notch3','Cx3cl1',
                                               'Lpl', 'Aqp7', 'Timp4',
                                               'Col15a1', 'Col4a2', 'Serpine1', 'Vwa1'
                                              ], cmap = 'viridis')

fig = plt.gcf() # 현재 모든 figure 가져오기
for ax in fig.get_axes(): # subplot에 모든 axes에 접근
    ax.grid(False)

plt.show()

In [ ]:
adata.obs['Annotation']=adata.obs['Annotation'].cat.reorder_categories(['liver', 'muscle/heart', 'intestine'])

In [ ]:
sc.pl.violin(adata, keys=['palantir_pseudotime'], groupby= 'Annotation', inner='box', rotation=90)

In [ ]:
adata.obs['annotation_ENDO_publish'] = adata.obs['annotation_ENDO_publish'].cat.reorder_categories(['Midzone','CV','PV','Fibrotic EC'])

In [ ]:
sc.pl.violin(adata, keys=['palantir_pseudotime'], groupby= 'annotation_ENDO_publish', inner='box', rotation=90)

In [ ]:
sc.pl.violin(adata, keys=['palantir_pseudotime'], groupby= 'annotation_endonew_publish', inner='box', rotation=90)

In [ ]:
## write
adata.write('../Write/240828_ECatlas-oldFiNi_combined_v02.h5ad')

# cellrank 

In [ ]:
import cellrank as cr

In [ ]:
import scvelo as scv

In [ ]:
adata = sc.read('../Write/240828_ECatlas-oldFiNi_combined_v02.h5ad')

In [ ]:
adata.uns['iroot']

In [ ]:
sc.pl.draw_graph(adata, color=['dpt_pseudotime'], cmap= 'Spectral_r')

In [ ]:
pk = cr.kernels.PseudotimeKernel(adata, time_key="dpt_pseudotime")
pk.compute_transition_matrix()
pk.plot_projection(basis="draw_graph_fa", recompute=True)

In [ ]:
ax = scv.pl.velocity_embedding_stream(adata, vkey='T_fwd', basis='draw_graph_fa', size=0, show=False)
sc.pl.draw_graph(adata, color=['annotation_endonew_publish'], ax=ax)

In [ ]:
ax = scv.pl.velocity_embedding_stream(adata, vkey='T_fwd', basis='draw_graph_fa', size=0, show=False)
sc.pl.draw_graph(adata, color=['dpt_pseudotime'], ax=ax)

In [ ]:
ax = scv.pl.velocity_embedding_stream(adata, vkey='T_fwd', basis='draw_graph_fa', size=0, show=False)
sc.pl.draw_graph(adata, color=['palantir_pseudotime'], ax=ax)

# fate probs 

In [ ]:
adata.obsm['palantir_fate_probabilities']

In [ ]:
df = adata.obs[['Annotation','annotation_ENDO_publish', 'annotation_endonew_publish', 'palantir_pseudotime']].join(adata.obsm['palantir_fate_probabilities'])
df

In [ ]:
df['merged_annotation'] = np.where(df['Annotation'].isna(), df['annotation_ENDO_publish'], df['Annotation'])

In [ ]:
sns.violinplot(df, x='PV', y = 'annotation_ENDO_publish')

In [ ]:
sns.violinplot(df, x='CV', y = 'annotation_ENDO_publish')

In [ ]:
sns.violinplot(df, x='EC_Col15a1', y = 'annotation_ENDO_publish')

In [ ]:
sns.violinplot(df, x='EC_Lpl', y = 'annotation_ENDO_publish')

In [ ]:
sns.violinplot(df, x='EC_Col15a1', y = 'annotation_endonew_publish')

In [ ]:
sns.violinplot(df, x='EC_Lpl', y = 'annotation_endonew_publish')

In [ ]:
sns.scatterplot(df, x='palantir_pseudotime', y='PV')

In [ ]:
sns.scatterplot(df, x='palantir_pseudotime', y='EC_Col15a1', hue = 'merged_annotation')

In [ ]:
ax = sns.scatterplot(df, x='palantir_pseudotime', y='EC_Col15a1', color = 'gray')
sns.scatterplot(df,  x='palantir_pseudotime', y='EC_Col15a1', hue = 'annotation_endonew_publish')

In [ ]:
sns.scatterplot(df, x='palantir_pseudotime', y='EC_Lpl', hue = 'merged_annotation')
plt.legend(loc= 'upper right', bbox_to_anchor=(1.5, 1))

In [ ]:
ax = sns.scatterplot(df, x='palantir_pseudotime', y='EC_Lpl', color = 'gray')
sns.scatterplot(df,  x='palantir_pseudotime', y='EC_Lpl', hue = 'annotation_endonew_publish')
plt.legend(loc= 'upper right', bbox_to_anchor=(1.5, 1))

# shared genes contributing to siumilarity

In [ ]:
figure, axis = plt.subplots(1, 2, figsize= (10, 5))
sc.pl.umap(adata, color = 'leiden_1.0', ax = axis[0], show=False)
axis[0].get_legend().remove()
sc.pl.draw_graph(adata, color = 'leiden_1.0', ax = axis[1], show=False)

In [ ]:
sc.pl.draw_graph(adata, color = 'annotation_endonew_publish')

In [ ]:
m = scl.markers.marker(adata, 'leiden_1.0')

In [ ]:
marker = m.plot_marker()

In [ ]:
marker['3'] # Col15a1

In [ ]:
sc.pl.draw_graph(adata, color = marker['3'], cmap='Spectral_r', ncols=5)

In [ ]:
fini.obs  = fini.obs.join(fini_new.obs['annotation_endonew_publish'])

In [ ]:
sc.pl.umap(fini, color = 'annotation_endonew_publish')

In [ ]:
sc.pl.umap(fini, color = marker['3'], cmap='Spectral_r', ncols=5)

In [ ]:
sc.pl.umap(atlas, color = marker['3'], cmap='Spectral_r', ncols=5)

In [ ]:
marker['12'] # Sele

In [ ]:
sc.pl.draw_graph(adata, color = marker['12'], cmap='Spectral_r', ncols=5)

In [ ]:
sc.pl.umap(fini, color = marker['12'], cmap='Spectral_r', ncols=5)

In [ ]:
sc.pl.umap(atlas, color = marker['12'], cmap='Spectral_r', ncols=5)

In [ ]:
marker['9'] # Sema3g

In [ ]:
sc.pl.draw_graph(adata, color = marker['9'], cmap='Spectral_r', ncols=5)

In [ ]:
sc.pl.umap(fini, color = marker['9'], cmap='Spectral_r', ncols=5)

In [ ]:
sc.pl.umap(atlas, color = marker['9'], cmap='Spectral_r', ncols=5)

# Senmayo Gene set

In [ ]:
with open('~/source/senmayo.txt', 'rb') as lf:
    senmayo = pickle.load(lf)
    print(readList)

In [ ]:
ec = ec.raw.to_adata()

In [ ]:
sc.tl.score_genes(ec, gene_list=senmayo, score_name='senmayo')
scl.us(adata, 'senmayo')

In [ ]:
sc.pl.umap(ec, color='senmayo', cmap='RdBu_r', vmax=0.5, show=False)
savefig(path, 'senmayo_score_umap')

In [ ]:
sns.set_style('ticks')
sc.pl.violin(ec[ec.obs['fibrotic_ec']=='yes'], 'sen_new', groupby='annolv3_EC', palette=fibec.uns['annolv3_EC_colors'], show=False)
savefig(path, 'violin_senmayo')

In [ ]:
ec.obs['fibrotic_ec'] = 'no'
ec.obs.loc[ec.obs['annolv2_EC']=='Fibrotic_EC', 'fibrotic_ec'] = 'yes'

In [ ]:
scl.us(ec, 'fibrotic_ec')

In [ ]:
fib_vol = volcano_analysis(ec, 'fibrotic_ec','yes','no')

In [ ]:
fib_vol

In [ ]:
fib_deg_1 = pd.DataFrame()
fib_deg_1['pval'] = fib_vol.pval
fib_deg_1['fc'] = fib_vol.fc
fib_deg_1['genelist'] = fib_vol.genelist
fib_deg_1['-log10pval'] = -np.log10(fib_deg_1['pval'])

In [ ]:
fib_gs = fib_deg_1[fib_deg_1['pval']<0.05]

In [ ]:
rnk = fib_gs[['genelist','fc']].rename(columns={'genelist':0,'fc':1})

In [ ]:
pre_res = gp.prerank(rnk=rnk,
                     gene_sets={'Senmayo':senmayo},
                     threads=4,
                     min_size=5,
                     max_size=1000,
                     permutation_num=1000, # reduce number to speed up testing
                     outdir=None, # don't write to disk
                     seed=6,
                     verbose=True, # see what's going on behind the scenes
                    )

In [ ]:
terms = pre_res.res2d.Term
sns.set_style('ticks')
axs = pre_res.plot(terms=terms[0])